In [1]:
import numpy as np
import pandas as pd
from ydata_profiling import ProfileReport

df = pd.DataFrame(np.random.rand(100, 5), columns=["a", "b", "c", "d", "e"])

In [2]:
profile = ProfileReport(df, title="Profiling Report")

In [3]:
profile

Render HTML: 100%|██████████| 1/1 [00:00<00:00,  4.06it/s]


In [4]:
profile.to_file("eda_pandas.html")

Export report to file: 100%|██████████| 1/1 [00:00<00:00, 525.40it/s]


In [1]:
def calculate_tax_comparison(income, mortgage_interest, property_tax, 
                           charitable_donations, state_local_tax,
                           child_tax_credit=2000):
    """
    Calculate and compare taxes using standard vs itemized deductions
    for married filing jointly with one child
    
    Parameters:
    income: Annual household income
    mortgage_interest: Annual mortgage interest paid
    property_tax: Annual property tax paid
    charitable_donations: Annual charitable contributions
    state_local_tax: State and local taxes paid
    child_tax_credit: Child tax credit amount (default $2000)
    """
    # 2024 tax brackets for married filing jointly
    tax_brackets = [
        (0, 22000, 0.10),
        (22000, 89450, 0.12),
        (89450, 190750, 0.22),
        (190750, 364200, 0.24),
        (364200, 462500, 0.32),
        (462500, 693750, 0.35),
        (693750, float('inf'), 0.37)
    ]
    
    # 2024 standard deduction for married filing jointly
    standard_deduction = 27700
    
    # Calculate itemized deductions
    salt_cap = 10000  # State and Local Tax deduction cap
    total_salt = min(state_local_tax + property_tax, salt_cap)
    
    itemized_deductions = (mortgage_interest + 
                          total_salt + 
                          charitable_donations)
    
    def calculate_tax(taxable_income):
        tax = 0
        for lower, upper, rate in tax_brackets:
            if taxable_income > lower:
                taxable_in_bracket = min(taxable_income - lower, upper - lower)
                tax += taxable_in_bracket * rate
        return tax
    
    # Calculate taxes both ways
    standard_taxable_income = max(income - standard_deduction, 0)
    itemized_taxable_income = max(income - itemized_deductions, 0)
    
    standard_tax = calculate_tax(standard_taxable_income)
    itemized_tax = calculate_tax(itemized_taxable_income)
    
    # Apply child tax credit
    standard_tax = max(standard_tax - child_tax_credit, 0)
    itemized_tax = max(itemized_tax - child_tax_credit, 0)
    
    return {
        'Standard Deduction': {
            'Deduction Amount': standard_deduction,
            'Taxable Income': standard_taxable_income,
            'Tax Before Credits': calculate_tax(standard_taxable_income),
            'Final Tax': standard_tax
        },
        'Itemized Deduction': {
            'Total Deductions': itemized_deductions,
            'Deduction Breakdown': {
                'Mortgage Interest': mortgage_interest,
                'SALT (capped)': total_salt,
                'Charitable Donations': charitable_donations
            },
            'Taxable Income': itemized_taxable_income,
            'Tax Before Credits': calculate_tax(itemized_taxable_income),
            'Final Tax': itemized_tax
        },
        'Difference': abs(standard_tax - itemized_tax),
        'Better Option': 'Standard Deduction' if standard_tax <= itemized_tax else 'Itemized Deduction'
    }

In [8]:
calculate_tax_comparison(250000, 38000, 450, 500, 5, 2000)

{'Standard Deduction': {'Deduction Amount': 27700,
  'Taxable Income': 222300,
  'Tax Before Credits': 40152.0,
  'Final Tax': 38152.0},
 'Itemized Deduction': {'Total Deductions': 38955,
  'Deduction Breakdown': {'Mortgage Interest': 38000,
   'SALT (capped)': 455,
   'Charitable Donations': 500},
  'Taxable Income': 211045,
  'Tax Before Credits': 37450.8,
  'Final Tax': 35450.8},
 'Difference': 2701.199999999997,
 'Better Option': 'Itemized Deduction'}

In [6]:
3000 * 12

36000